# Basic Exploratory Data Analysis

## Description of the data

The dataset contains the following fields:

- `price`
- `model_year`
- `model`
- `condition`
- `cylinders`
- `fuel`
- `odometer`
- `transmission`
- `type`
- `paint_color`
- `is_4wd`
- `date_posted`
- `days_listed`

## Imports

In [1]:
import pandas as pd
import numpy as np

print("pandas version: " + pd.__version__)
print("numpy version: " + np.__version__)

pandas version: 2.2.2
numpy version: 2.1.0


In [2]:
# visualization module
import plotly.express as px

## Input Data

In [3]:
vehicles = pd.read_csv("../vehicles_us.csv")
vehicles.head(10)

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   
5  14990      2014.0    chrysler 300  excellent        6.0  gas   57954.0   
6  12990      2015.0    toyota camry  excellent        4.0  gas   79212.0   
7  15990      2013.0     honda pilot  excellent        6.0  gas  109473.0   
8  11500      2012.0     kia sorento  excellent        4.0  gas  104174.0   
9   9200      2008.0     honda pilot  excellent        NaN  gas  147191.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28  
5    automatic   sedan       black     1.0  2018-06-20           15  
6    automatic   sedan       white     NaN  2018-12-27           73  
7    automatic     SUV       black     1.0  2019-01-07           68  
8    automatic     SUV         NaN     1.0  2018-07-16           19  
9    automatic     SUV        blue     1.0  2019-02-15           17

In [4]:
vehicles.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


Infering that the price column is the target variable and the other 12 columns are in this case the features. Four features are numerical, while the other nine are categorical. None of the `float64` fields actually utilize the features of the float data type, so they should be changed to `int64` or into other more appropriate data types. For example, `is_4wd` is a float but should be represented as a categorical variable. The `date_posted` column should be converted to a `date_time` format. There are missing values in the `model_year`, `cylinders`, `odometer`, `paint_color`, `is_4wd`.

## Handling missing data

Before and data type conversion can be completed. The missing values must be handled. The following operations handle the missing data by either dropping or filling them. First we drop data that can't confidently be filled.

In [5]:
# Drop missing values from model_year, and cylinders

vehicles = vehicles.dropna(subset=['model_year', 'cylinders'])

We drop the missing values in `model_year`, and `cylinders` because these are non-negotiable and there is no real way to fill the missing values with applicable data.

The rest of the features will be handled accordingly:

- `odometer` : fill missing values with the median
- `paint_color` : fill with `unknown` there are too many missing values that wont really contribute as an important feature so dropping values (+8000 rows of the entire dataset) doesn't seem like a good idea.
- `is_4wd` : fill with `0`. Many of the missing values here must represent the boolean opposite of `1.0`.


In [6]:
# Fill NA paint_color
vehicles['paint_color'] = vehicles['paint_color'].fillna('unknown')

In [7]:
# Fill NA odomerter
vehicles['odometer'] = vehicles['odometer'].fillna(vehicles['odometer'].median())

In [8]:
# Fill NA is_4wd
vehicles['is_4wd'] = vehicles['is_4wd'].fillna(0)

In [9]:
# Check for NA values
vehicles.isnull().sum()

price           0
model_year      0
model           0
condition       0
cylinders       0
fuel            0
odometer        0
transmission    0
type            0
paint_color     0
is_4wd          0
date_posted     0
days_listed     0
dtype: int64

There are no longer any null values in the `vehicles` dataframe. Now we can appropriately update the data types of the feature columns in question.

In [10]:
vehicles = vehicles.astype({'is_4wd': 'int64', 'odometer': 'int64', 'cylinders': 'int64', 'model_year': 'int64'})
vehicles.info()

<class 'pandas.core.frame.DataFrame'>
Index: 43009 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   price         43009 non-null  int64 
 1   model_year    43009 non-null  int64 
 2   model         43009 non-null  object
 3   condition     43009 non-null  object
 4   cylinders     43009 non-null  int64 
 5   fuel          43009 non-null  object
 6   odometer      43009 non-null  int64 
 7   transmission  43009 non-null  object
 8   type          43009 non-null  object
 9   paint_color   43009 non-null  object
 10  is_4wd        43009 non-null  int64 
 11  date_posted   43009 non-null  object
 12  days_listed   43009 non-null  int64 
dtypes: int64(6), object(7)
memory usage: 4.6+ MB


## Non-exact duplicate handling

In [11]:
num_models = vehicles['model'].nunique()
print("Number of unique car models in the vehicle data set:", num_models)

Number of unique car models in the vehicle data set: 100


With 100 unique vehicle models to inspect, there are enough to go about figuring out the exact matches in a more programatic way. Utilizing the built-in `difflib` package we can determine close matches within the `model` column. From this we can then swiftly handle each.

In [13]:
import difflib

vehicle_models = vehicles['model'].unique()

potential_duplicates = []

# Compare each model with every other model
for i, model in enumerate(vehicle_models):
    matches = difflib.get_close_matches(model, vehicle_models[i+1:], n=5, cutoff=0.8)
    if matches:
        potential_duplicates.append((model, matches))

# Convert potential duplicates to a DataFrame
potential_duplicates_df = pd.DataFrame(potential_duplicates, columns=['Model', 'Potential Duplicates'])

print(potential_duplicates_df)



                            Model  \
0                  hyundai sonata   
1                      ford f-150   
2                    chrysler 200   
3                    toyota camry   
4        chevrolet silverado 1500   
5                        ram 1500   
6                   jeep cherokee   
7             chevrolet silverado   
8                chevrolet malibu   
9                  ford fusion se   
10                  nissan altima   
11            jeep grand cherokee   
12                     ford focus   
13                    honda civic   
14     chevrolet silverado 3500hd   
15                  ford f-250 sd   
16  chevrolet silverado 1500 crew   
17           ford f250 super duty   
18                  ford f-350 sd   
19                     ford f-250   
20                      ford f150   
21                     gmc sierra   
22           ford f350 super duty   
23              gmc sierra 2500hd   
24                       ram 3500   
25                      ford f250   



From the close match search there are 25 vehicle models that could potentially be duplicated in a non-exact manner.

Vehicle Model Non-Exact Duplicate Analysis:

- `ford f-150`, `ford f150` were quickly detected as non-exact duplicates.
- chevrolet silverado `xxxx` has a couple of distinct model names, however some just appear as `chevrolet silverado`.
  - Must investigate these occurrences further.
- Many models have the prefix model name, while similar models from the same manufacture will add different features. For example: `toyota camry - toyota camry le`, `ford fusion - ford fusion se`. For the purposes of this analysis, close-matches like these will be disregarded.



In [23]:
silverado_models = vehicles[vehicles['model'].str.contains('silverado', case=False)]['model'].unique()
silverado_models_count = vehicles[vehicles['model'].str.contains('silverado', case=False)]['model'].value_counts()

print("Unique Chevrolet Silverado Models: \n", silverado_models)
print("\n")
print("Count of Chevrolet Silverado Models: \n", silverado_models_count)

Unique Chevrolet Silverado Models: 
 ['chevrolet silverado 1500' 'chevrolet silverado'
 'chevrolet silverado 3500hd' 'chevrolet silverado 1500 crew'
 'chevrolet silverado 2500hd']


Count of Chevrolet Silverado Models: 
 model
chevrolet silverado 1500         1802
chevrolet silverado              1043
chevrolet silverado 2500hd        778
chevrolet silverado 1500 crew     250
chevrolet silverado 3500hd        208
Name: count, dtype: int64


All the silverado models appear to be unique. However, the difficulty lies in the presence of `chevrolet silverado` which is not an exact model name. For this reason, we will remove all occurrences of `chevrolet silverado`.

In [26]:
vehicles = vehicles[vehicles['model'].str.lower() != 'chevrolet silverado']
silverado_models = vehicles[vehicles['model'].str.contains('silverado', case=False)]['model'].unique()
print(silverado_models)

['chevrolet silverado 1500' 'chevrolet silverado 3500hd'
 'chevrolet silverado 1500 crew' 'chevrolet silverado 2500hd']


Now the `chevrolet silverado` entries are removed, and we can focus on other close matches within the vehicles `model` feature by standardization. 

In [27]:
# Standardize Ford F-XXX
vehicles['model'].replace('ford f150', 'ford f-150', inplace=True)
vehicles['model'].replace('ford f250', 'ford f-250', inplace=True)
vehicles['model'].replace('ford f350', 'ford f-350', inplace=True)

num_models2 = vehicles['model'].nunique()
print("Number of unique car models in the vehicle data set after standardization:", num_models2)

Number of unique car models in the vehicle data set after standardization: 97


## `date_posted` data type

In [31]:
vehicles['date_posted'] = pd.to_datetime(vehicles['date_posted'])
print(vehicles.info())
vehicles.head()

<class 'pandas.core.frame.DataFrame'>
Index: 41966 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         41966 non-null  int64         
 1   model_year    41966 non-null  int64         
 2   model         41966 non-null  object        
 3   condition     41966 non-null  object        
 4   cylinders     41966 non-null  int64         
 5   fuel          41966 non-null  object        
 6   odometer      41966 non-null  int64         
 7   transmission  41966 non-null  object        
 8   type          41966 non-null  object        
 9   paint_color   41966 non-null  object        
 10  is_4wd        41966 non-null  int64         
 11  date_posted   41966 non-null  datetime64[ns]
 12  days_listed   41966 non-null  int64         
dtypes: datetime64[ns](1), int64(6), object(6)
memory usage: 4.5+ MB
None


price  model_year           model  condition  cylinders fuel  odometer  \
0   9400        2011          bmw x5       good          6  gas    145000   
2   5500        2013  hyundai sonata   like new          4  gas    110000   
3   1500        2003      ford f-150       fair          8  gas    113000   
4  14900        2017    chrysler 200  excellent          4  gas     80903   
5  14990        2014    chrysler 300  excellent          6  gas     57954   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV     unknown       1  2018-06-23           19  
2    automatic   sedan         red       0  2019-02-07           79  
3    automatic  pickup     unknown       0  2019-03-22            9  
4    automatic   sedan       black       0  2019-04-02           28  
5    automatic   sedan       black       1  2018-06-20           15

## Basic EDA

In [94]:
# Histogram of car prices
fig = px.histogram(vehicles, x='price', nbins=45, 
                   title='Distribution of Car Prices',
                   labels={'price': 'Price ($)'},
                   color_discrete_sequence=['#003f5c'],  # Custom color
                   marginal='box',  # Add a box plot for more stats
                   height=300,
                   width=500)

fig.update_layout(
    xaxis_title='Price ($)',
    yaxis_title='Vehicle Count',
    title_font_size=15,
    title_x=0.5
)

fig.show()


In [61]:
fig = px.scatter(vehicles, x='odometer', y='price', 
                 title='Price vs. Odometer',
                 labels={'odometer': 'Odometer (miles)', 'price': 'Price ($)'},
                 color='model_year',  # Color by model year
                 opacity=0.8,
                 trendline='ols',  # Add a trend line
                 height=350)

fig.update_layout(
    title_font_size=15,
    title_x=0.5
)

fig.show()


In [34]:
unique_conditions = vehicles['condition'].unique()
unique_conditions

array(['good', 'like new', 'fair', 'excellent', 'salvage', 'new'],
      dtype=object)

In [86]:
avg_price_by_condition = vehicles.groupby('condition')['price'].mean().reset_index()
avg_price_by_condition.columns = ['condition', 'average_price']


fig = px.bar(avg_price_by_condition, x='condition', y='average_price', 
             title='Average Price by Condition', 
             labels={'condition': 'Condition', 'average_price': 'Average Price ($)'},
             color='condition',
             text='average_price',
             color_discrete_map={
                 'excellent': '#003f5c',
                 'fair': '#444e86',
                 'good': '#955196',
                 'like new': '#dd5182',
                 'new': '#ff6e54',
                 'salvage': '#ffa600'
             }, 
             height=350,
             template='plotly_white') 

fig.update_traces(texttemplate='%{text:.2s}', textposition='inside',
                  marker=dict(line=dict(color='black', width=1)))  # Add border around bars

fig.update_layout(
    title_font_size=15,
    title_x=0.5,
    xaxis=dict(tickangle=-45)  # Rotate x-axis labels
)

fig.show()

